# Ideales Gas

Standardimports und Funktion, um die Simulation durch Schließen des Fensters zu beenden

In [1]:
using PyCall
using PyPlot
pygui(true)
using StatsBase

function handle_close(event)
    global update_figure
    update_figure = false
end

handle_close (generic function with 1 method)

Funktion, um die Kollision zweier Teilchen zu berechnen

In [2]:
# particles: Array of dimension (4, n_particles) - the four entries are (r_x, r_y, v_x, v_y)
# dt: time step
# s: disc size - radius
@inbounds function overlap(particles, dt, s)        
    # masses of the particles if you want to play around with
    # unequal masses
    m1 = 1
    m2 = 1
    
    for p1 in 1:size(particles, 2)
        r1 = particles[1:2, p1]
        v1 = particles[3:4, p1]
        
        for p2 in p1 + 1:size(particles, 2)
            r2 = particles[1:2, p2]
            v2 = particles[3:4, p2]

            # Check overlap
            if ((r1[1] - r2[1])^2 + (r1[2] - r2[2])^2) <= 4 * s^2
                # ignore if velocity of both is zero
                if norm(v1) < 1e-10 && norm(v2) < 1e-10
                    continue end

                # Displace discs to remove overlap
                                    
                # Calculate new velocities 
                
                # Move particles one time step in direction of new velocities
            end
        end
    end
end

Die Funktion `euler_step` bewegt alle Teilchen um einen Zeitschritt. In `wall_collision` wird geprüft, ob ein Teilchen mit der Wand kollidiert und dann gegebenenfalls die Richtung des Impuls geändert werden muss.

In [3]:
# particles: Array of dimension (4, n_particles) - the four entries are (r_x, r_y, v_x, v_y)
# dt: time step
@inbounds function euler_step(particles, dt)
    for p in 1:size(particles, 2)
        particles[1, p] = particles[1, p] + particles[3, p] * dt
        particles[2, p] = particles[2, p] + particles[4, p] * dt
    end    
end

# particles: Array of dimension (4, n_particles) - the four entries are (r_x, r_y, v_x, v_y)
# dt: time step
# s: disc size - radius
@inbounds function wall_collision(particles, dt, s)
    for p in 1:size(particles, 2)
        move = false
        if particles[1, p] > 2 - s || particles[1, p] < -2 + s
            particles[3, p] *= -1    
            move = true
        end

        if particles[2, p] > 2 - s || particles[2, p] < -2 + s
            particles[4, p] *= -1
            move = true
        end
        
        if move
            particles[1:2, p] += particles[3:4, p] * dt
        end
    end    
end

In [4]:
# time step
dt = 0.01
# disc radius
s = 0.04
# number of particles
n_particles = 200

# Setup the particles array
particles = zeros(4, n_particles)
particles[1:2, :] = rand(2, n_particles) * 3.9 - 1.95
particles[3, 1] = 1
particles[4, 1] = 1

# Initialize  figure
fig = figure(figsize=(5, 6))
fig[:canvas][:mpl_connect]("close_event", handle_close)
ax = plt[:subplot2grid]((6, 1), (0, 0), rowspan=5)
ax[:xaxis][:set_visible](false)
ax[:yaxis][:set_visible](false)
ax[:set_facecolor]("grey")
ax[:set_xlim]([-2.0, 2.0])
ax[:set_ylim]([-2.0, 2.0])
ax2 = plt[:subplot2grid]((6, 1), (5, 0))
ax2[:xaxis][:set_visible](false)
ax2[:yaxis][:set_visible](false)
ax2[:set_facecolor]("grey")
plt[:tight_layout]()

# Plot initial configuration
# The colors of the points are chosen according to the absolute values of the velocities from the colormap "hot"
vs = sqrt(particles[3, :, 1].^2 + particles[4, :, 1].^2)
p_plot = ax[:scatter](particles[1, :, 1], particles[2, :, 1], c=vs / maximum(vs), cmap="hot")

# Display the histogram
h = fit(Histogram, vs, nbins=20, closed=:left)
shrink_factors = [0., 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0]
# colors are chosen according to the velocity bins
hist_scatters = [ax2[:scatter](h.edges[1][2:end], f * h.weights, c=h.edges[1][2:end] / maximum(h.edges[1][2:end]), cmap="hot") for f in shrink_factors]
cmap = matplotlib[:cm][:get_cmap]("hot")

# =====================================================
# Run simulation
# =====================================================

update_figure = true
i = 0
while update_figure   
    euler_step(particles, dt)
    wall_collision(particles, dt, s)    
    overlap(particles, dt, s)

    # display only every tenth step
    if i == 10
        # reassign colors and replot points
        vs = sqrt(particles[3, :].^2 + particles[4, :].^2)
        new_colors = cmap(vs / maximum(vs))
        p_plot[:set_facecolors](new_colors)    
        p_plot[:set_offsets](particles[1:2, :]')
        
        # redraw histogram
        h = fit(Histogram, vs, linspace(minimum(vs), maximum(vs), 20), closed=:left)        
        h_colors = cmap(h.edges[1][2:end] / maximum(h.edges[1][2:end]))        
        for (i, f) in enumerate(shrink_factors)
            hist_scatters[i][:set_offsets]([h.edges[1][2:end] f * h.weights])
            hist_scatters[i][:set_facecolors](h_colors)
        end
        ax2[:set_xlim]([h.edges[1][1], h.edges[1][end] * 1.05])
        ax2[:set_ylim]([0, maximum(h.weights) * 1.2])
        
        pause(1e-15)    
        i = 0
    end
    i += 1
end

/Users/peter/.julia/v0.5/Conda/deps/usr/lib/python2.7/site-packages/matplotlib/backend_bases.py:2453: MatplotlibDeprecationWarning: Using default event loop until function specific to this GUI is implemented
  warnings.warn(str, mplDeprecation)
